In [1]:
import numpy as np
import pandas as pd
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
output_notebook()

data = pd.read_csv("./asm_data_for_ml.txt", sep='\t')
X = np.c_[data.MJD, data.orbit, data.rateA, data.rateB, data.rateC, data.rateC / data.rateA, data.rate]
X_plot = np.c_[data.rateC / data.rateA, data.rate]

Loading BokehJS ...

In [2]:
from bokeh.io import vform
from bokeh.models import CustomJS, ColumnDataSource, Slider
from bokeh.plotting import Figure, output_file, show

# output_file("callback.html")

#time_var = X[:, 1]  # data.orbit
time_var = X[:, 0]  # data.MJD
step =(time_var.max() - time_var.min()) / 1000

source = ColumnDataSource(data=dict(x=X_plot[:, 0], y=X_plot[:, 1], time_var=time_var, 
                                    x_keep=X_plot[:, 0], y_keep=X_plot[:, 1]))

plot = Figure(plot_width=400, plot_height=400, x_range=[0, 5], y_range=[0, 200])
plot.circle('x', 'y', source=source)

# callback = CustomJS(args=dict(source=source), code="""
#         var data = source.get('data');
#         var o = cb_obj.get('value')
#         x = data['x'][time_var <= o]
#         y = data['y'][time_var <= o]
#         source.trigger('change');
#     """)
# slider = Slider(start=0, end=1, value=0, step=.01, title="", callback=callback)

def callback(source=source):
    data = source.get('data')
    f = cb_obj.get('value')
    x, y, time_var, x_keep, y_keep = data['x'], data['y'], data['time_var'], data['x_keep'], data['y_keep']
    
    # no way to enter the step in callback! (columndatasource imposes all columns to have the same size):
    step = (max(time_var) - min(time_var)) / 1000
    # we cannot just do:  (why? no idea.)
    # x = x[time_var <= f]
    # y = y[time_var <= f]
    for i in range(len(x)):
        if time_var[i] > f and time_var[i] < f + step:
            x[i] = x_keep[i]
            y[i] = y_keep[i]
        else:
            x[i] = 0
            y[i] = 0
    source.trigger('change')

slider = Slider(start=time_var.min(), end=time_var.max(), value=time_var.min(), step=step,
                title="", callback=CustomJS.from_py_func(callback))

layout = vform(slider, plot)

show(layout)